<div class="bg-primary text-info"><br><center><h1>TP 19bis - Recherche par dichotomie dans une liste triée</h1></center><br></div>

Vous avez déjà joué au jeu _"Trouve un nombre entre 1 et 10"_ et proposé 5. Si la réponse est _"Plus grand"_ vous proposez 7 puis si l'on vous répond _"Plus petit"_ vous proposez 6...  

Vous avez effectué une **recherche par dichotomie** !

Faire une recherche dichotomique, c'est chercher une valeur dans un tableau en prenant le milieu de l'ensemble des solutions possibles (qui sont donc **triées**) pour éliminer la moitié des possibilités à chaque étape.

---
## Création d'une liste

En vous inspirant des TP 18 sur les tuples et 19 sur les listes, écrivez une fonction nommée ```liste_entiers_au_hasard``` paramétrée par un entier ```n```, qui renvoie une liste de n d'entiers choisis aléatoirement entre 1 et n.


```
liste_entiers_au_hasard(10)
# doit renvoyer par exemple [2, 0, 6, 6, 1, 7, 6, 4, 7, 2]
```

In [1]:
from random import*

def liste_entiers_au_hasard (n):        
    l=[randint(1,n) for i in range(n)]
    return l

In [2]:
# Vérification
liste_entiers_au_hasard(10)

[4, 1, 9, 10, 9, 7, 6, 5, 8, 6]

---
## Tri d'une liste

Nous étudierons plus tard cette année différents algorithmes de tri, mais il existe une méthode ```sort``` permettant de trier une liste.  
Vérifiez la méthode avec le code ci-dessous :

In [3]:
# Génération d'une liste avec notre fonction précédente
maliste = liste_entiers_au_hasard(20)

# Affichage de la liste
print ("Liste non triée :\t",maliste)

# Tri de la liste
maliste.sort()

# Affichage de la liste
print ("Liste triée :\t\t",maliste)

Liste non triée :	 [19, 13, 17, 20, 7, 9, 17, 4, 8, 4, 14, 20, 17, 1, 6, 19, 10, 12, 7, 6]
Liste triée :		 [1, 4, 4, 6, 6, 7, 7, 8, 9, 10, 12, 13, 14, 17, 17, 17, 19, 19, 20, 20]


---
## Suppression des doublons

Lors du TP 19 sur les listes (Exercice 6) vous avez développé la fonction ```doublons``` qui supprime les éléments en double. Nous pourrions l'utiliser ici pour notre liste, cependant elle ne serait pas assez performante sur des listes de grande taille.

La ligne de code suivant permet d'extraire les valeurs uniques d'une liste (```set```) puis d'en générer une nouvelle liste (```list```)

In [4]:
list(set(maliste))

[1, 4, 6, 7, 8, 9, 10, 12, 13, 14, 17, 19, 20]

---
## Recherche par méthode brute

### Implémentation de la méthode brute
La première méthode qui nous viendra naturellement pour rechercher un élément dans une liste est la méthode brute.  
Elle consiste à parcourir la liste dans l'ordre dans une boucle et comparer chaque élément à l'élément recherché.  
Si l'élément en cours est l'élément recherché alors la fonction s'arrête et renvoie ```True```.


Ecrivez ci-dessous une fonction ```recherche_brute```qui prend en paramètres un élément ```elt``` et une liste ```liste```et renvoie ```True``` si l'élément est trouvé ou ```False``` sinon. 

Votre fonction devra parcourir la liste élément par élément et les comparer au paramètre ```elt```.

In [5]:
def recherche_brute (elt, maliste):
    for e in maliste:
        if elt==e:
            return True
    return False

In [6]:
# Vérification
recherche_brute(19,[0, 2, 4, 5, 6, 8, 9, 10, 11, 12, 13, 15, 17, 19, 20])

True

### Performance de la méthode brute

- Pour mesurer le temps d'exécution d'une fonction, on peut utiliser le module ```timeit```, les lignes suivantes permettront d'effectuer cette mesure en secondes et de la stocker dans la variable ```temps``` :
``` Python
from timeit import default_timer as timer
debut_chrono = timer()
#code à mesurer
fin_chrono = timer()
duree = fin_chrono - debut_chrono
```


Testez ce code suivant en mesurant la durée de génération d'une liste de 100 000 entiers choisis aléatoirement.

In [9]:
from timeit import default_timer as timer
debut_chrono = timer()
maliste = liste_entiers_au_hasard(100000)

fin_chrono = timer()
duree = fin_chrono - debut_chrono
duree

0.38599999999996726

- Ecrivez maintenant un programme qui : 
    1. Génère une liste de 100 000 entiers au hasard
    2. Trie la liste
    3. Supprime les doublons de la liste
    4. Recherche l'entier 100 000 dans la liste avec la fonction ```recherche_brute``` (pire des cas)
    5. Affichera si l'entier à été trouvé et en quelle durée

*Note : Vous pouvez multiplier les durées par 1000 pour avoir un résultat en millisecondes qui sera plus lisible*

<center><span style="color:red"><b><font size="3">
Attention, sauvegardez votre notebook avant de vous lancer dans l'écriture d'une fonction qui traite un gros volume de données...
</font></b></span></center>

In [8]:
from timeit import default_timer as timer
debut_chrono = timer()
elt=100000
maliste = liste_entiers_au_hasard(elt)
maliste.sort()
maliste=list(set(maliste))
test=recherche_brute(elt, maliste)
# print (maliste,"\n")
print(test)

fin_chrono = timer()
duree = fin_chrono - debut_chrono
duree*1000

True


494.99999999989086

---
## Recherche par dichotomie

### Implémentation de la méthode

Imaginons que nous recherchions une personne dans un annuaire classé par ordre alphabétique
- On ouvre l’annuaire au centre
- La personne est soit sur cette page, soit avant soit après
- En supposant qu’elle soit avant (on la recherchera donc dans la première moitié de l’annuaire)
- On ouvre la page du milieu de cette première moitié...
- On recommence jusqu’à obtenir la bonne page ou conclure que la personne n’est pas dans l’annuaire

Soit ```liste``` une liste triée et ```elt``` l’élément à chercher, l'algorithme qui implémente cette méthode est le suivant :

```
    debut ← 0
    fin ← Indice du dernier élément de la liste
    Tant que debut <= fin faire
        milieu=(debut+fin)//2
        Si liste[milieu] = elt alors
            retourner True
        Sinon
            Si liste[milieu] < elt alors
                debut ← milieu+1
            Sinon
                fin ← milieu-1
    retourner False
```


A l'aide de cet algorithme, ecrivez ci-dessous une fonction ```recherche_dicho```qui prend en paramètres un élément ```elt``` et une liste ```liste```et renvoie ```True``` si l'élément est trouvé ou ```False``` sinon.

In [13]:
def recherche_dicho (elt,liste):
    debut=0
    fin=len(liste)-1
    while debut<=fin:
        milieu=(debut+fin)//2
        if liste[milieu]==elt:
            return True
        else:
            if liste[milieu]<elt:
                debut=milieu+1
            else:
                fin=milieu-1
    return False


In [14]:
# Vérification
recherche_dicho(100,[0, 2, 4, 5, 6, 8, 9, 10, 11, 12, 13, 15, 17, 19, 20])

False

### Performance de la recherche dichotomique
- Ecrivez maintenant un programme qui : 
    1. Génère une liste de 100 000 entiers au hasard
    2. Trie la liste
    3. Supprime les doublons de la liste
    4. Recherche l'entier 100 000 dans la liste avec la fonction ```recherche_dicho``` (pire des cas)
    5. Affichera si l'entier à été trouvé et en quelle durée

*Note : Vous pouvez multiplier les durées par 1000 pour avoir un résultat en millisecondes qui sera plus lisible*

In [21]:
from timeit import default_timer as timer

elt=100000
maliste = liste_entiers_au_hasard(elt)
maliste.sort()

maliste=list(set(maliste))

debut_chrono = timer()
rechd=recherche_dicho (elt,maliste)


fin_chrono = timer()
duree = fin_chrono - debut_chrono
duree*1000

0.0

### Comparatif entre les deux méthodes
- Ecrivez maintenant un programme qui : 
    1. Génère une liste de 100 000 entiers au hasard
    2. Trie la liste
    3. Supprime les doublons de la liste
    4. Recherche l'entier 100 000 dans la liste avec la fonction ```recherche_dicho``` (pire des cas)
    5. Recherche l'entier 100 000 dans la liste avec la fonction ```recherche_dicho```
    5. Affiche si l'entier à été trouvé et en quelle durée pour chacune des deux recherches

*Note : Vous pouvez multiplier les durées par 1000 pour avoir un résultat en millisecondes qui sera plus lisible*

In [22]:
from timeit import default_timer as timer
debut_chronob = timer()
debut_chronod = timer()
maliste = liste_entiers_au_hasard(100000)
maliste=list(set(maliste))
maliste.sort()

debut_chronob = timer()
rechb=recherche_brute (elt,maliste)

debut_chronod = timer()
rechd=recherche_dicho (elt,maliste)

fin_chronob = timer()
dureeb = fin_chronob - debut_chronob
print("BRUTE:",dureeb*1000)


fin_chronod = timer()
dureed = fin_chronod - debut_chronod
print("DICHO:",dureed*1000)


BRUTE: 7.000000000061846
DICHO: 0.0


- Modifiez maintenant votre code pour augmenter le nombre d'éléments et affiner votre comparaison.

---
## Complexité des deux méthodes de recherche

### Recherche brute
Pour effectuer une recherche brute, nous allons successivement comparer l'élément recherché avec les éléments de la liste.  
Si nous sommes dans le pire des cas : l'élément est le dernier de la liste, nous allons donc effectuer autant de comparaisons que d'éléments dans la liste.  
Si ```n``` est le nombre d'éléments dans la liste nous effectuerons donc **n** comparaisons.

La complexité de la recherche brute est donc **linéaire**


### Recherche dichotomique
Pour effectuer une recherche dichotomique, nous allons comparer l'élément recherché l'élément central de la liste puis couper la liste en deux.  
Dans le pire des cas : l'élément est le dernier de la liste (ou le premier), nous diviser successivement le nombre d'éléments de la liste par 2.  
Si ```n``` est le nombre d'éléments dans la liste nous effectuerons donc **log<sub>2</sub>(n)** comparaisons.

La complexité de la recherche dichotomique est donc **logarithmique**


### Exemples :
Prenons par exemple la liste triée suivante :  

```[0, 3, 4, 5, 6, 9, 10, 11, 12, 14, 15, 16, 21, 23, 24, 26, 27, 30, 31, 34, 36, 37, 38, 39, 40, 43, 44, 47, 48, 50, 51, 52]```

Elle contient 32 éléments, recherchons le dernier élément ```52```:

#### Recherche brute :
- Nous allons comparer 52 à tous les éléments un par un de 0 à 52 pour finalement le trouver.  
=> Le nombre de comparaisons est de **32** soit le nombre d'éléments dans la liste 

#### Recherche dichotomique :
- Nous comparons 52 à l'élément central : 26 -> 1 comparaison
- Nous divisons la liste en deux et le nombre est plus grand
- Nous comparons 52 à l'élément central de la nouvelle liste : 39 -> 2 comparaisons
- Nous divisons la liste en deux et le nombre est plus grand
- Nous comparons 52 à l'élément central de la nouvelle liste : 47 -> 3 comparaisons
- Nous divisons la liste en deux et le nombre est plus grand
- Nous comparons 52 à l'élément central de la nouvelle liste : 51 -> 4 comparaisons
- Nous divisons la liste en deux et le nombre est plus grand
- Nous comparons 52 à l'élément central de la nouvelle liste : 52 -> 5 comparaisons  
=> Le nombre de comparaisons est donc  : **5** soit **log<sub>2</sub>(32)** (car **2<sup>5</sup>=32**)
